In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
import matplotlib.pyplot as plt
from sklearn.tree import DecisionTreeClassifier, export_text
from sklearn.tree import _tree
from sklearn.preprocessing import KBinsDiscretizer
import numpy as np
import re
import random
import copy
import json

In [2]:
# Script Outline
# Input: row
# Output: paths(num >=1)
# For each entry, there should be (path, prediction, accuracy, the missing features)
# Path shoud have a dict of each values 
# Note: There should be a measture for the missing features
#       Broken Path(features all missing) should be handled

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
pd.set_option('display.max_rows', None)  # None means unlimited
pd.set_option('display.max_columns', None)  # None means unlimited
pd.set_option('display.width', 1000)  # Adjust width to accommodate more columns

In [5]:
random.seed(42)

In [6]:
numerical_features = [
    'flow_duration', 'Header_Length', 'Duration', 'Rate',
    'Srate', 'Drate', 'ack_count','syn_count','fin_count','urg_count',
    'rst_count','Tot_sum', 'Min', 'Max', 'AVG', 'Std',
    'Tot_size', 'IAT', 'Number', 'Magnitue', 'Radius',
    'Covariance', 'Variance', 'Weight'
]

flag_features = [
    'HTTP', 'HTTPS', 'DNS', 'Telnet',
    'SMTP', 'SSH', 'IRC', 'TCP', 'UDP', 'DHCP', 'ARP',
    'ICMP', 'IPv', 'LLC'
]

all_features = [
    'flow_duration', 'Header_Length', 'Duration', 'Rate',
    'Srate', 'Drate', 'ack_count','syn_count','fin_count','urg_count',
    'rst_count','Tot_sum', 'Min', 'Max', 'AVG', 'Std',
    'Tot_size', 'IAT', 'Number', 'Magnitue', 'Radius',
    'Covariance', 'Variance', 'Weight',
    'HTTP', 'HTTPS', 'DNS', 'Telnet',
    'SMTP', 'SSH', 'IRC', 'TCP', 'UDP', 'DHCP', 'ARP',
    'ICMP', 'IPv', 'LLC',
    'fin_flag_number', 'syn_flag_number', 'rst_flag_number',
    'psh_flag_number', 'ack_flag_number', 'ece_flag_number', 'cwr_flag_number'
]
#4 6 6 5 3 4 7 3 3 4

In [7]:
df = pd.read_csv('../source/combined_test.csv')
df = df.groupby('label').sample(n=625, random_state=42)
df.rename(columns={'Tot sum': 'Tot_sum'}, inplace=True)
df.rename(columns={'Tot size': 'Tot_size'}, inplace=True)
df.rename(columns={'Protocol Type': 'Protocol_Type'}, inplace=True)

In [8]:
all_entries_res = []

In [9]:
def classify(data):
    global all_entries_res
    potential_paths = []
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] > 9.28) or (data['Number'] == -1)) and ((data['Number'] <= 9.56) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] > 292.18) or (data['Tot_size'] == -1)) and ((data['Tot_size'] <= 902.01) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['Header_Length'] <= 150021.5) or (data['Header_Length'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Header_Length': data['Header_Length'], 'TCP': data['TCP']}
        potential_paths.append([feature_dict, 'Web-Based', 38.2])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] <= 11.5) or (data['Number'] == -1)) and ((data['Number'] > 7.5) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['Header_Length'] <= 150021.5) or (data['Header_Length'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Header_Length': data['Header_Length'], 'TCP': data['TCP']}
        potential_paths.append([feature_dict, 'Brute_Force', 35.6])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 133481500.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] <= 5.41) or (data['Radius'] == -1)) and ((data['Tot_sum'] <= 700.96) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] > 166551400.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] > 19281.41) or (data['Covariance'] == -1)) and ((data['Min'] <= 67.95) or (data['Min'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Min': data['Min'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'BenignTraffic', 81.16])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.2) or (data['flow_duration'] == -1)) and ((data['Covariance'] > 81486.11) or (data['Covariance'] == -1)) and ((data['Tot_size'] > 350.8) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Covariance': data['Covariance'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Spoofing', 96.8])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] > 19281.41) or (data['Covariance'] == -1)) and ((data['Min'] > 67.95) or (data['Min'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'BenignTraffic', 70.74])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] > 167246344.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] <= 873.25) or (data['Max'] == -1)) and ((data['ack_count'] <= 0.13) or (data['ack_count'] == -1)) and ((data['fin_count'] <= 0.08) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'ack_count': data['ack_count'], 'fin_count': data['fin_count']}
        potential_paths.append([feature_dict, 'Brute_Force', 30.6])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] > 873.25) or (data['Max'] == -1)) and ((data['Variance'] <= 0.97) or (data['Variance'] == -1)) and ((data['Header_Length'] <= 156572.95) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Brute_Force', 36.8])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] > 873.25) or (data['Max'] == -1)) and ((data['Variance'] > 0.97) or (data['Variance'] == -1)) and ((data['syn_count'] > 0.65) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'Brute_Force', 55.25])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] <= 166551400.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 166499176.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 85.75) or (data['Tot_size'] == -1)) and ((data['Tot_sum'] <= 3884.2) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Tot_size': data['Tot_size'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Recon', 51.53])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] <= 166551400.0) or (data['IAT'] == -1)) and ((data['IAT'] > 166499176.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] <= 79.94) or (data['Weight'] == -1)) and ((data['UDP'] <= 0.5) or (data['UDP'] == -1)) and ((data['Radius'] <= 753.63) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'UDP': data['UDP'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Brute_Force', 38.51])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] > 0.47) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] > 19281.41) or (data['Covariance'] == -1)) and ((data['Min'] <= 67.95) or (data['Min'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Min': data['Min'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'BenignTraffic', 62.38])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] > 167246344.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.39) or (data['flow_duration'] == -1)) and ((data['AVG'] <= 380.76) or (data['AVG'] == -1)) and ((data['Weight'] > 77.83) or (data['Weight'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'AVG': data['AVG'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] <= 873.25) or (data['Max'] == -1)) and ((data['ack_count'] > 0.13) or (data['ack_count'] == -1)) and ((data['Max'] > 140.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'ack_count': data['ack_count']}
        potential_paths.append([feature_dict, 'Web-Based', 31.59])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] <= 11.14) or (data['Magnitue'] == -1)) and ((data['IAT'] <= 166850840.0) or (data['IAT'] == -1)) and ((data['Max'] > 54.2) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 19281.41) or (data['Covariance'] == -1)) and ((data['Header_Length'] <= 220049.1) or (data['Header_Length'] == -1)) and ((data['IAT'] <= 166551376.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'BenignTraffic', 33.65])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] <= 79.94) or (data['Weight'] == -1)) and ((data['UDP'] <= 0.5) or (data['UDP'] == -1)) and ((data['Radius'] > 753.63) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'UDP': data['UDP'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Spoofing', 39.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] <= 79.94) or (data['Weight'] == -1)) and ((data['UDP'] > 0.5) or (data['UDP'] == -1)) and ((data['Srate'] > 29.92) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'UDP': data['UDP'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Spoofing', 91.95])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] > 7.5) or (data['Number'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] > 1.32) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Recon', 93.35])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] <= 18379.3) or (data['Covariance'] == -1)) and ((data['syn_count'] > 0.15) or (data['syn_count'] == -1)) and ((data['Radius'] > 69.8) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Recon', 42.62])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.2) or (data['flow_duration'] == -1)) and ((data['Covariance'] > 81486.11) or (data['Covariance'] == -1)) and ((data['Tot_size'] <= 350.8) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Covariance': data['Covariance'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Spoofing', 90.72])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 19281.41) or (data['Covariance'] == -1)) and ((data['Header_Length'] > 220049.1) or (data['Header_Length'] == -1)) and ((data['IAT'] <= 166473832.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'BenignTraffic', 72.88])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] <= 60.5) or (data['Min'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)) and ((data['Max'] <= 80.8) or (data['Max'] == -1)) and ((data['rst_flag_number'] <= 0.5) or (data['rst_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number'], 'Max': data['Max'], 'rst_flag_number': data['rst_flag_number']}
        potential_paths.append([feature_dict, 'Recon', 99.62])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] > 557.26) or (data['Tot_sum'] == -1)) and ((data['Rate'] > 3.37) or (data['Rate'] == -1)) and ((data['ICMP'] <= 0.5) or (data['ICMP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Rate': data['Rate'], 'ICMP': data['ICMP']}
        potential_paths.append([feature_dict, 'DoS', 79.09])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] <= 221395.0) or (data['Header_Length'] == -1)) and ((data['rst_count'] <= 240.9) or (data['rst_count'] == -1)) and ((data['AVG'] > 98.91) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Spoofing', 41.63])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] > 79.94) or (data['Weight'] == -1)) and ((data['Variance'] > 0.83) or (data['Variance'] == -1)) and ((data['Tot_size'] > 478.82) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'DDoS', 74.77])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] > 114.73) or (data['Rate'] == -1)) and ((data['Min'] <= 1504.0) or (data['Min'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'Min': data['Min'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Spoofing', 94.47])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] > 79.94) or (data['Weight'] == -1)) and ((data['Variance'] <= 0.83) or (data['Variance'] == -1)) and ((data['rst_count'] <= 5.44) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Mirai', 95.26])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] <= 1398.8) or (data['Tot_sum'] == -1)) and ((data['syn_count'] <= 1.75) or (data['syn_count'] == -1)) and ((data['Protocol_Type'] <= 10.7) or (data['Protocol_Type'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Protocol_Type': data['Protocol_Type']}
        potential_paths.append([feature_dict, 'Recon', 98.09])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] <= 60.5) or (data['Min'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)) and ((data['Max'] <= 80.8) or (data['Max'] == -1)) and ((data['rst_flag_number'] > 0.5) or (data['rst_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number'], 'Max': data['Max'], 'rst_flag_number': data['rst_flag_number']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] > 79.94) or (data['Weight'] == -1)) and ((data['Variance'] > 0.83) or (data['Variance'] == -1)) and ((data['Tot_size'] <= 478.82) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Recon', 86.57])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['AVG'] > 60.58) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'HTTPS': data['HTTPS'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'BenignTraffic', 78.17])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 19281.41) or (data['Covariance'] == -1)) and ((data['Header_Length'] > 220049.1) or (data['Header_Length'] == -1)) and ((data['IAT'] > 166473832.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'BenignTraffic', 98.46])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 3.07) or (data['flow_duration'] == -1)) and ((data['Duration'] <= 246.5) or (data['Duration'] == -1)) and ((data['IAT'] > 166729192.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Web-Based', 67.02])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] <= 64.31) or (data['Max'] == -1)) and ((data['AVG'] <= 56.22) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['Header_Length'] > 150021.5) or (data['Header_Length'] == -1)) and ((data['Protocol_Type'] <= 12.65) or (data['Protocol_Type'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Header_Length': data['Header_Length'], 'Protocol_Type': data['Protocol_Type']}
        potential_paths.append([feature_dict, 'BenignTraffic', 59.78])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] > 873.25) or (data['Max'] == -1)) and ((data['Variance'] <= 0.97) or (data['Variance'] == -1)) and ((data['Header_Length'] > 156572.95) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'BenignTraffic', 49.72])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] <= 166551400.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 166499176.0) or (data['IAT'] == -1)) and ((data['Tot_size'] <= 85.75) or (data['Tot_size'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'Recon', 86.98])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] > 1382.54) or (data['AVG'] == -1)) and ((data['IAT'] <= 83219648.01) or (data['IAT'] == -1)) and ((data['urg_count'] > 86.1) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['Header_Length'] > 150021.5) or (data['Header_Length'] == -1)) and ((data['Protocol_Type'] > 12.65) or (data['Protocol_Type'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Header_Length': data['Header_Length'], 'Protocol_Type': data['Protocol_Type']}
        potential_paths.append([feature_dict, 'Spoofing', 92.59])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)) and ((data['Covariance'] <= 90.4) or (data['Covariance'] == -1)) and ((data['flow_duration'] <= 38.82) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Covariance': data['Covariance'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] <= 1382.54) or (data['AVG'] == -1)) and ((data['Variance'] <= 0.95) or (data['Variance'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Spoofing', 90.84])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 19281.41) or (data['Covariance'] == -1)) and ((data['Header_Length'] <= 220049.1) or (data['Header_Length'] == -1)) and ((data['IAT'] > 166551376.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] <= 0.38) or (data['Std'] == -1)) and ((data['ack_flag_number'] > 0.5) or (data['ack_flag_number'] == -1)) and ((data['IAT'] <= 166729200.0) or (data['IAT'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'ack_flag_number': data['ack_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] > 873.25) or (data['Max'] == -1)) and ((data['Variance'] > 0.97) or (data['Variance'] == -1)) and ((data['syn_count'] <= 0.65) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'BenignTraffic', 64.75])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] <= 166551400.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 166499176.0) or (data['IAT'] == -1)) and ((data['Tot_size'] <= 85.75) or (data['Tot_size'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'Recon', 55.37])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['IAT'] <= 41462536.02) or (data['IAT'] == -1)) and ((data['Magnitue'] <= 11.04) or (data['Magnitue'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'Recon', 83.48])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Min'] <= 786.0) or (data['Min'] == -1)) and ((data['rst_count'] <= 115.55) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Recon', 25.22])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] <= 114.73) or (data['Rate'] == -1)) and ((data['urg_count'] <= 340.9) or (data['urg_count'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'BenignTraffic', 75.45])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] <= 18379.3) or (data['Covariance'] == -1)) and ((data['syn_count'] > 0.15) or (data['syn_count'] == -1)) and ((data['Radius'] <= 69.8) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Spoofing', 58.88])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] > 18379.3) or (data['Covariance'] == -1)) and ((data['IAT'] <= 166846232.0) or (data['IAT'] == -1)) and ((data['Duration'] <= 160.4) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Web-Based', 78.5])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] > 1382.54) or (data['AVG'] == -1)) and ((data['IAT'] <= 83219648.01) or (data['IAT'] == -1)) and ((data['urg_count'] <= 86.1) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 85.71])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 3.07) or (data['flow_duration'] == -1)) and ((data['flow_duration'] > 3.52) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 732.1) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Spoofing', 71.15])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] > 12.75) or (data['Number'] == -1)) and ((data['IAT'] <= 166551400.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 166499176.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 85.75) or (data['Tot_size'] == -1)) and ((data['Tot_sum'] > 3884.2) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Tot_size': data['Tot_size'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Recon', 84.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] <= 0.38) or (data['Std'] == -1)) and ((data['ack_flag_number'] > 0.5) or (data['ack_flag_number'] == -1)) and ((data['IAT'] > 166729200.0) or (data['IAT'] == -1)) and ((data['AVG'] > 66.04) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'ack_flag_number': data['ack_flag_number'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Web-Based', 97.98])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] > 7715.2) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 12.1) or (data['urg_count'] == -1)) and ((data['Covariance'] <= 1051078.34) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Spoofing', 48.94])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.39) or (data['flow_duration'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['Number'] <= 6.0) or (data['Number'] == -1)) and ((data['Tot_sum'] > 354.75) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'TCP': data['TCP'], 'Number': data['Number'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 86.96])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] <= 20.54) or (data['flow_duration'] == -1)) and ((data['Tot_sum'] > 442.75) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Min'] <= 786.0) or (data['Min'] == -1)) and ((data['rst_count'] > 115.55) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Web-Based', 37.36])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['IAT'] <= 41462536.02) or (data['IAT'] == -1)) and ((data['Magnitue'] > 11.04) or (data['Magnitue'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'Brute_Force', 40.45])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] > 557.26) or (data['Tot_sum'] == -1)) and ((data['Rate'] <= 3.37) or (data['Rate'] == -1)) and ((data['IAT'] <= 83022948.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] > 4.3) or (data['rst_count'] == -1)) and ((data['Tot_sum'] <= 1616.65) or (data['Tot_sum'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Spoofing', 84.88])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] <= 0.38) or (data['Std'] == -1)) and ((data['ack_flag_number'] <= 0.5) or (data['ack_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'ack_flag_number': data['ack_flag_number']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 3.07) or (data['flow_duration'] == -1)) and ((data['Duration'] <= 246.5) or (data['Duration'] == -1)) and ((data['IAT'] <= 166729192.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] <= 18379.3) or (data['Covariance'] == -1)) and ((data['syn_count'] <= 0.15) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 72.36) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Recon', 85.71])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.2) or (data['flow_duration'] == -1)) and ((data['Covariance'] <= 81486.11) or (data['Covariance'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Covariance': data['Covariance'], 'TCP': data['TCP']}
        potential_paths.append([feature_dict, 'Spoofing', 91.18])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] <= 4.3) or (data['rst_count'] == -1)) and ((data['Covariance'] > 6269.43) or (data['Covariance'] == -1)) and ((data['Rate'] > 28.62) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] > 284.45) or (data['rst_count'] == -1)) and ((data['Covariance'] > 19281.41) or (data['Covariance'] == -1)) and ((data['Min'] > 67.95) or (data['Min'] == -1)) and ((data['psh_flag_number'] > 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 71.43])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] <= 79.94) or (data['Weight'] == -1)) and ((data['UDP'] > 0.5) or (data['UDP'] == -1)) and ((data['Srate'] <= 29.92) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'UDP': data['UDP'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Spoofing', 37.1])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] > 56.38) or (data['Tot_size'] == -1)) and ((data['IAT'] > 41462904.01) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] <= 221395.0) or (data['Header_Length'] == -1)) and ((data['rst_count'] <= 240.9) or (data['rst_count'] == -1)) and ((data['AVG'] <= 98.91) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Spoofing', 65.57])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] <= 3093.8) or (data['Max'] == -1)) and ((data['Weight'] <= 90.03) or (data['Weight'] == -1)) and ((data['rst_count'] <= 1266.6) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Web-Based', 31.67])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] > 14.65) or (data['urg_count'] == -1)) and ((data['Tot_size'] <= 2347.6) or (data['Tot_size'] == -1)) and ((data['Header_Length'] <= 1000736.09) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'BenignTraffic', 31.03])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] <= 4.3) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 6269.43) or (data['Covariance'] == -1)) and ((data['UDP'] > 0.5) or (data['UDP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'UDP': data['UDP']}
        potential_paths.append([feature_dict, 'Spoofing', 90.91])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] <= 873.25) or (data['Max'] == -1)) and ((data['ack_count'] <= 0.13) or (data['ack_count'] == -1)) and ((data['fin_count'] > 0.08) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'ack_count': data['ack_count'], 'fin_count': data['fin_count']}
        potential_paths.append([feature_dict, 'Brute_Force', 54.55])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 3.07) or (data['flow_duration'] == -1)) and ((data['flow_duration'] > 3.52) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 732.1) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Spoofing', 52.83])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] > 4.3) or (data['rst_count'] == -1)) and ((data['Tot_sum'] > 1616.65) or (data['Tot_sum'] == -1)) and ((data['urg_count'] <= 64.35) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 292.85) or (data['Rate'] == -1)) and ((data['rst_count'] <= 284.45) or (data['rst_count'] == -1)) and ((data['Max'] <= 873.25) or (data['Max'] == -1)) and ((data['ack_count'] > 0.13) or (data['ack_count'] == -1)) and ((data['Max'] <= 140.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'rst_count': data['rst_count'], 'Max': data['Max'], 'ack_count': data['ack_count']}
        potential_paths.append([feature_dict, 'Brute_Force', 36.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] > 1398.8) or (data['Tot_sum'] == -1)) and ((data['Header_Length'] <= 23286.3) or (data['Header_Length'] == -1)) and ((data['Radius'] > 81.55) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Recon', 73.47])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] > 20.54) or (data['flow_duration'] == -1)) and ((data['Min'] <= 67.7) or (data['Min'] == -1)) and ((data['Srate'] > 1.34) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Brute_Force', 57.45])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] > 14.65) or (data['urg_count'] == -1)) and ((data['Tot_size'] <= 2347.6) or (data['Tot_size'] == -1)) and ((data['Header_Length'] > 1000736.09) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'BenignTraffic', 87.23])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] > 5.41) or (data['Radius'] == -1)) and ((data['Magnitue'] <= 10.39) or (data['Magnitue'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] <= 20.54) or (data['flow_duration'] == -1)) and ((data['Tot_sum'] <= 442.75) or (data['Tot_sum'] == -1)) and ((data['Tot_size'] <= 66.45) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Tot_sum': data['Tot_sum'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] <= 0.38) or (data['Std'] == -1)) and ((data['ack_flag_number'] > 0.5) or (data['ack_flag_number'] == -1)) and ((data['IAT'] > 166729200.0) or (data['IAT'] == -1)) and ((data['AVG'] <= 66.04) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'ack_flag_number': data['ack_flag_number'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Web-Based', 65.12])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] <= 221395.0) or (data['Header_Length'] == -1)) and ((data['rst_count'] > 240.9) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 4959.5) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Recon', 76.74])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] <= 7715.2) or (data['Header_Length'] == -1)) and ((data['rst_count'] <= 39.4) or (data['rst_count'] == -1)) and ((data['Covariance'] > 86125.98) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Recon', 51.22])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.2) or (data['flow_duration'] == -1)) and ((data['Rate'] <= 1169.08) or (data['Rate'] == -1)) and ((data['fin_count'] <= 0.35) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate'], 'fin_count': data['fin_count']}
        potential_paths.append([feature_dict, 'Spoofing', 53.66])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] > 114.73) or (data['Rate'] == -1)) and ((data['Min'] > 1504.0) or (data['Min'] == -1)) and ((data['Duration'] <= 57.0) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'Min': data['Min'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] > 11.12) or (data['Magnitue'] == -1)) and ((data['Duration'] <= 100.6) or (data['Duration'] == -1)) and ((data['syn_count'] > 0.1) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'Duration': data['Duration'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'Brute_Force', 56.1])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 188.85) or (data['urg_count'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] <= 6170.85) or (data['rst_count'] == -1)) and ((data['Tot_sum'] > 435.1) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 92.5])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] <= 11.14) or (data['Magnitue'] == -1)) and ((data['IAT'] <= 166850840.0) or (data['IAT'] == -1)) and ((data['Max'] <= 54.2) or (data['Max'] == -1)) and ((data['AVG'] > 53.88) or (data['AVG'] == -1)) and ((data['Rate'] > 7.23) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Max': data['Max'], 'AVG': data['AVG'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] > 466.88) or (data['Max'] == -1)) and ((data['Weight'] > 79.94) or (data['Weight'] == -1)) and ((data['Variance'] <= 0.83) or (data['Variance'] == -1)) and ((data['rst_count'] > 5.44) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'DoS', 60.53])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] <= 11.12) or (data['Magnitue'] == -1)) and ((data['syn_flag_number'] > 0.5) or (data['syn_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'syn_flag_number': data['syn_flag_number']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.0) or (data['IAT'] == -1)) and ((data['Magnitue'] > 53.6) or (data['Magnitue'] == -1)) and ((data['Header_Length'] > 427410.41) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Magnitue': data['Magnitue'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] <= 0.38) or (data['Std'] == -1)) and ((data['ack_flag_number'] > 0.5) or (data['ack_flag_number'] == -1)) and ((data['IAT'] <= 166729200.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'ack_flag_number': data['ack_flag_number']}
        potential_paths.append([feature_dict, 'BenignTraffic', 59.46])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] <= 14.65) or (data['urg_count'] == -1)) and ((data['Header_Length'] > 180764.0) or (data['Header_Length'] == -1)) and ((data['Radius'] > 48.07) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Spoofing', 66.67])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] > 7.5) or (data['Number'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] <= 1.32) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'DoS', 58.33])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] > 4.3) or (data['rst_count'] == -1)) and ((data['Tot_sum'] > 1616.65) or (data['Tot_sum'] == -1)) and ((data['urg_count'] > 64.35) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 75.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] <= 14.65) or (data['urg_count'] == -1)) and ((data['Header_Length'] <= 180764.0) or (data['Header_Length'] == -1)) and ((data['ack_flag_number'] > 0.5) or (data['ack_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'ack_flag_number': data['ack_flag_number']}
        potential_paths.append([feature_dict, 'Web-Based', 46.88])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.2) or (data['flow_duration'] == -1)) and ((data['Rate'] > 1169.08) or (data['Rate'] == -1)) and ((data['Tot_sum'] <= 37934.4) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Min'] > 786.0) or (data['Min'] == -1)) and ((data['Rate'] <= 106.78) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Min': data['Min'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Web-Based', 72.41])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] <= 1382.54) or (data['AVG'] == -1)) and ((data['Variance'] <= 0.95) or (data['Variance'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'BenignTraffic', 35.71])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] <= 3093.8) or (data['Max'] == -1)) and ((data['Weight'] <= 90.03) or (data['Weight'] == -1)) and ((data['rst_count'] > 1266.6) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Web-Based', 75.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] > 3093.8) or (data['Max'] == -1)) and ((data['Covariance'] <= 2317899.75) or (data['Covariance'] == -1)) and ((data['Number'] <= 9.5) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Covariance': data['Covariance'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'Spoofing', 67.86])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] > 18379.3) or (data['Covariance'] == -1)) and ((data['IAT'] > 166846232.0) or (data['IAT'] == -1)) and ((data['urg_count'] <= 36.65) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 81.48])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] > 221395.0) or (data['Header_Length'] == -1)) and ((data['Radius'] > 56.66) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] <= 140.4) or (data['Weight'] == -1)) and ((data['Protocol_Type'] <= 25.4) or (data['Protocol_Type'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 25.51) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Protocol_Type': data['Protocol_Type'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Spoofing', 32.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] > 114.73) or (data['Rate'] == -1)) and ((data['Min'] > 1504.0) or (data['Min'] == -1)) and ((data['Duration'] > 57.0) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'Min': data['Min'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 92.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.0) or (data['IAT'] == -1)) and ((data['Magnitue'] <= 53.6) or (data['Magnitue'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Magnitue': data['Magnitue'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'Spoofing', 48.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] > 7715.2) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 12.1) or (data['urg_count'] == -1)) and ((data['Max'] <= 3076.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Spoofing', 91.67])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] > 11.12) or (data['Magnitue'] == -1)) and ((data['Duration'] > 100.6) or (data['Duration'] == -1)) and ((data['Max'] <= 90.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'Duration': data['Duration'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'BenignTraffic', 69.57])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] <= 1382.54) or (data['AVG'] == -1)) and ((data['Variance'] > 0.95) or (data['Variance'] == -1)) and ((data['syn_count'] <= 0.25) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'BenignTraffic', 68.18])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] > 7715.2) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 12.1) or (data['urg_count'] == -1)) and ((data['Covariance'] > 1051078.34) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Spoofing', 80.95])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] <= 3093.8) or (data['Max'] == -1)) and ((data['Weight'] > 90.03) or (data['Weight'] == -1)) and ((data['rst_count'] > 89.1) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'BenignTraffic', 61.9])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] <= 203.92) or (data['AVG'] == -1)) and ((data['IAT'] > 166850728.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] > 11.12) or (data['Magnitue'] == -1)) and ((data['Duration'] <= 100.6) or (data['Duration'] == -1)) and ((data['syn_count'] <= 0.1) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'Duration': data['Duration'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'Spoofing', 90.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] <= 221395.0) or (data['Header_Length'] == -1)) and ((data['rst_count'] > 240.9) or (data['rst_count'] == -1)) and ((data['Covariance'] > 4959.5) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Spoofing', 60.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] <= 4.3) or (data['rst_count'] == -1)) and ((data['Covariance'] > 6269.43) or (data['Covariance'] == -1)) and ((data['Rate'] <= 28.62) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Spoofing', 89.47])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] > 126.97) or (data['Weight'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] > 60.5) or (data['Min'] == -1)) and ((data['SSH'] <= 0.5) or (data['SSH'] == -1)) and ((data['Covariance'] > 1.12) or (data['Covariance'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'SSH': data['SSH'], 'Covariance': data['Covariance'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Brute_Force', 78.95])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.39) or (data['flow_duration'] == -1)) and ((data['AVG'] > 380.76) or (data['AVG'] == -1)) and ((data['Duration'] > 61.5) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'AVG': data['AVG'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.2) or (data['flow_duration'] == -1)) and ((data['Covariance'] <= 81486.11) or (data['Covariance'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Covariance': data['Covariance'], 'TCP': data['TCP']}
        potential_paths.append([feature_dict, 'Spoofing', 38.89])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] > 20.54) or (data['flow_duration'] == -1)) and ((data['Min'] <= 67.7) or (data['Min'] == -1)) and ((data['Srate'] <= 1.34) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Recon', 44.44])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] > 60.5) or (data['Min'] == -1)) and ((data['SSH'] <= 0.5) or (data['SSH'] == -1)) and ((data['Covariance'] <= 1.12) or (data['Covariance'] == -1)) and ((data['Header_Length'] <= 27577.7) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'SSH': data['SSH'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Recon', 77.78])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['IAT'] > 41462536.02) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] <= 11.14) or (data['Magnitue'] == -1)) and ((data['IAT'] <= 166850840.0) or (data['IAT'] == -1)) and ((data['Max'] <= 54.2) or (data['Max'] == -1)) and ((data['AVG'] > 53.88) or (data['AVG'] == -1)) and ((data['Rate'] <= 7.23) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Max': data['Max'], 'AVG': data['AVG'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Recon', 94.12])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] <= 18379.3) or (data['Covariance'] == -1)) and ((data['syn_count'] <= 0.15) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 72.36) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Recon', 47.06])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] <= 5.41) or (data['Radius'] == -1)) and ((data['Tot_sum'] > 700.96) or (data['Tot_sum'] == -1)) and ((data['Magnitue'] > 10.68) or (data['Magnitue'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Tot_sum': data['Tot_sum'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'Spoofing', 93.75])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] <= 203.92) or (data['AVG'] == -1)) and ((data['IAT'] <= 166850728.0) or (data['IAT'] == -1)) and ((data['Duration'] <= 116.55) or (data['Duration'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Duration': data['Duration'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 56.25])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] > 18379.3) or (data['Covariance'] == -1)) and ((data['IAT'] > 166846232.0) or (data['IAT'] == -1)) and ((data['urg_count'] > 36.65) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Recon', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] <= 20.54) or (data['flow_duration'] == -1)) and ((data['Tot_sum'] <= 442.75) or (data['Tot_sum'] == -1)) and ((data['Tot_size'] > 66.45) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Tot_sum': data['Tot_sum'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Brute_Force', 80.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] > 0.02) or (data['IAT'] == -1)) and ((data['Number'] <= 7.01) or (data['Number'] == -1)) and ((data['Tot_sum'] <= 303.1) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Brute_Force', 57.14])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] > 114.73) or (data['Rate'] == -1)) and ((data['Min'] <= 1504.0) or (data['Min'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'Min': data['Min'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'BenignTraffic', 53.85])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.39) or (data['flow_duration'] == -1)) and ((data['AVG'] <= 380.76) or (data['AVG'] == -1)) and ((data['Weight'] <= 77.83) or (data['Weight'] == -1)) and ((data['AVG'] > 59.13) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'AVG': data['AVG'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'Spoofing', 92.31])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['flow_duration'] <= 17.93) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['IAT'] > 78690612.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] > 5.41) or (data['Radius'] == -1)) and ((data['Magnitue'] > 10.39) or (data['Magnitue'] == -1)) and ((data['Max'] <= 74.7) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Magnitue': data['Magnitue'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Brute_Force', 41.67])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] <= 4.3) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 6269.43) or (data['Covariance'] == -1)) and ((data['UDP'] <= 0.5) or (data['UDP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance'], 'UDP': data['UDP']}
        potential_paths.append([feature_dict, 'Spoofing', 58.33])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] > 60.5) or (data['Min'] == -1)) and ((data['SSH'] <= 0.5) or (data['SSH'] == -1)) and ((data['Covariance'] <= 1.12) or (data['Covariance'] == -1)) and ((data['Header_Length'] > 27577.7) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'SSH': data['SSH'], 'Covariance': data['Covariance'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Spoofing', 45.45])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] <= 114.73) or (data['Rate'] == -1)) and ((data['urg_count'] > 340.9) or (data['urg_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'urg_count': data['urg_count']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] > 3093.8) or (data['Max'] == -1)) and ((data['Covariance'] > 2317899.75) or (data['Covariance'] == -1)) and ((data['Duration'] > 62.75) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Covariance': data['Covariance'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'BenignTraffic', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] > 60.5) or (data['Min'] == -1)) and ((data['SSH'] > 0.5) or (data['SSH'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'SSH': data['SSH']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] > 1398.8) or (data['Tot_sum'] == -1)) and ((data['Header_Length'] > 23286.3) or (data['Header_Length'] == -1)) and ((data['IAT'] > 166729120.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Spoofing', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] > 0.02) or (data['ack_count'] == -1)) and ((data['Variance'] <= 0.64) or (data['Variance'] == -1)) and ((data['Min'] <= 290.12) or (data['Min'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Variance': data['Variance'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] <= 140.4) or (data['Weight'] == -1)) and ((data['Protocol_Type'] <= 25.4) or (data['Protocol_Type'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['SSH'] <= 0.5) or (data['SSH'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Protocol_Type': data['Protocol_Type'], 'HTTPS': data['HTTPS'], 'SSH': data['SSH']}
        potential_paths.append([feature_dict, 'Recon', 90.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 3.07) or (data['flow_duration'] == -1)) and ((data['flow_duration'] <= 3.52) or (data['flow_duration'] == -1)) and ((data['Rate'] <= 372.16) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] > 292.18) or (data['Tot_size'] == -1)) and ((data['Tot_size'] > 902.01) or (data['Tot_size'] == -1)) and ((data['Duration'] > 54.0) or (data['Duration'] == -1)) and ((data['IAT'] > 166849664.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] > 5.41) or (data['Radius'] == -1)) and ((data['Magnitue'] > 10.39) or (data['Magnitue'] == -1)) and ((data['Max'] > 74.7) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Magnitue': data['Magnitue'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Spoofing', 88.89])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] <= 3093.8) or (data['Max'] == -1)) and ((data['Weight'] > 90.03) or (data['Weight'] == -1)) and ((data['rst_count'] <= 89.1) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Weight': data['Weight'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Recon', 44.44])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] > 1398.8) or (data['Tot_sum'] == -1)) and ((data['Header_Length'] <= 23286.3) or (data['Header_Length'] == -1)) and ((data['Radius'] <= 81.55) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Spoofing', 77.78])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] <= 14.65) or (data['urg_count'] == -1)) and ((data['Header_Length'] > 180764.0) or (data['Header_Length'] == -1)) and ((data['Radius'] <= 48.07) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Mirai', 44.44])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] > 56.38) or (data['Tot_size'] == -1)) and ((data['IAT'] <= 41462904.01) or (data['IAT'] == -1)) and ((data['IAT'] <= 0.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] > 292.18) or (data['Tot_size'] == -1)) and ((data['Tot_size'] > 902.01) or (data['Tot_size'] == -1)) and ((data['Duration'] > 54.0) or (data['Duration'] == -1)) and ((data['IAT'] <= 166849664.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 77.78])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 3.07) or (data['flow_duration'] == -1)) and ((data['Duration'] > 246.5) or (data['Duration'] == -1)) and ((data['IAT'] > 166729152.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Recon', 87.5])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] > 3093.8) or (data['Max'] == -1)) and ((data['Covariance'] <= 2317899.75) or (data['Covariance'] == -1)) and ((data['Number'] > 9.5) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Covariance': data['Covariance'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'Brute_Force', 75.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] > 6.95) or (data['Srate'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Min'] > 786.0) or (data['Min'] == -1)) and ((data['Rate'] > 106.78) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'HTTPS': data['HTTPS'], 'Min': data['Min'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] <= 557.26) or (data['Tot_sum'] == -1)) and ((data['Srate'] <= 107.41) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] > 11.12) or (data['Magnitue'] == -1)) and ((data['Duration'] > 100.6) or (data['Duration'] == -1)) and ((data['Max'] > 90.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'Duration': data['Duration'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['AVG'] <= 60.58) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'HTTPS': data['HTTPS'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Web-Based', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] > 557.26) or (data['Tot_sum'] == -1)) and ((data['Rate'] > 3.37) or (data['Rate'] == -1)) and ((data['ICMP'] > 0.5) or (data['ICMP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Rate': data['Rate'], 'ICMP': data['ICMP']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['flow_duration'] > 17.93) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'BenignTraffic', 28.57])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] > 7.5) or (data['Number'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)) and ((data['flow_duration'] > 0.59) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'HTTP': data['HTTP'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'DDoS', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] <= 0.05) or (data['fin_count'] == -1)) and ((data['Covariance'] > 18379.3) or (data['Covariance'] == -1)) and ((data['IAT'] <= 166846232.0) or (data['IAT'] == -1)) and ((data['Duration'] > 160.4) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Covariance': data['Covariance'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 83.33])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] <= 7715.2) or (data['Header_Length'] == -1)) and ((data['rst_count'] <= 39.4) or (data['rst_count'] == -1)) and ((data['Covariance'] <= 86125.98) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Spoofing', 83.33])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] <= 140.4) or (data['Weight'] == -1)) and ((data['Protocol_Type'] > 25.4) or (data['Protocol_Type'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Protocol_Type': data['Protocol_Type']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.39) or (data['flow_duration'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['Number'] <= 6.0) or (data['Number'] == -1)) and ((data['Tot_sum'] <= 354.75) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'TCP': data['TCP'], 'Number': data['Number'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Brute_Force', 66.67])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] > 1398.8) or (data['Tot_sum'] == -1)) and ((data['Header_Length'] > 23286.3) or (data['Header_Length'] == -1)) and ((data['IAT'] <= 166729120.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] <= 140.4) or (data['Weight'] == -1)) and ((data['Protocol_Type'] <= 25.4) or (data['Protocol_Type'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] <= 25.51) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Protocol_Type': data['Protocol_Type'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Web-Based', 66.67])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] <= 11.12) or (data['Magnitue'] == -1)) and ((data['syn_flag_number'] <= 0.5) or (data['syn_flag_number'] == -1)) and ((data['IAT'] > 166605808.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'syn_flag_number': data['syn_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] > 1382.54) or (data['AVG'] == -1)) and ((data['IAT'] > 83219648.01) or (data['IAT'] == -1)) and ((data['rst_count'] <= 178.75) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.0) or (data['IAT'] == -1)) and ((data['Magnitue'] <= 53.6) or (data['Magnitue'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Magnitue': data['Magnitue'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] > 64.31) or (data['Max'] == -1)) and ((data['Max'] <= 364.0) or (data['Max'] == -1)) and ((data['fin_count'] <= 0.32) or (data['fin_count'] == -1)) and ((data['IAT'] <= 83165664.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] > 221395.0) or (data['Header_Length'] == -1)) and ((data['Radius'] <= 56.66) or (data['Radius'] == -1)) and ((data['Srate'] > 34.16) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] > 14.65) or (data['urg_count'] == -1)) and ((data['Tot_size'] > 2347.6) or (data['Tot_size'] == -1)) and ((data['Covariance'] <= 915674.0) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Tot_size': data['Tot_size'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Web-Based', 80.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] <= 7715.2) or (data['Header_Length'] == -1)) and ((data['rst_count'] > 39.4) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] > 0.45) or (data['syn_count'] == -1)) and ((data['Max'] > 3093.8) or (data['Max'] == -1)) and ((data['Covariance'] > 2317899.75) or (data['Covariance'] == -1)) and ((data['Duration'] <= 62.75) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'Max': data['Max'], 'Covariance': data['Covariance'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 75.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] <= 0.7) or (data['syn_count'] == -1)) and ((data['Rate'] <= 114.73) or (data['Rate'] == -1)) and ((data['urg_count'] <= 340.9) or (data['urg_count'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Rate': data['Rate'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] > 133481500.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 98.2) or (data['Tot_size'] == -1)) and ((data['syn_count'] <= 1.7) or (data['syn_count'] == -1)) and ((data['Rate'] > 74.44) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.39) or (data['flow_duration'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'TCP': data['TCP']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.39) or (data['flow_duration'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 6.0) or (data['Number'] == -1)) and ((data['Srate'] <= 695.91) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'TCP': data['TCP'], 'Number': data['Number'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] > 64.31) or (data['Max'] == -1)) and ((data['Max'] <= 364.0) or (data['Max'] == -1)) and ((data['fin_count'] > 0.32) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] <= 287.0) or (data['rst_count'] == -1)) and ((data['Srate'] <= 6.95) or (data['Srate'] == -1)) and ((data['flow_duration'] > 20.54) or (data['flow_duration'] == -1)) and ((data['Min'] > 67.7) or (data['Min'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Srate': data['Srate'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 188.85) or (data['urg_count'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] > 6170.85) or (data['rst_count'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'BenignTraffic', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] > 557.26) or (data['Tot_sum'] == -1)) and ((data['Rate'] <= 3.37) or (data['Rate'] == -1)) and ((data['IAT'] > 83022948.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.2) or (data['flow_duration'] == -1)) and ((data['Rate'] > 1169.08) or (data['Rate'] == -1)) and ((data['Tot_sum'] > 37934.4) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 75.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] > 1382.54) or (data['AVG'] == -1)) and ((data['IAT'] > 83219648.01) or (data['IAT'] == -1)) and ((data['rst_count'] > 178.75) or (data['rst_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG'], 'rst_count': data['rst_count']}
        potential_paths.append([feature_dict, 'BenignTraffic', 75.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 3.07) or (data['flow_duration'] == -1)) and ((data['Duration'] > 246.5) or (data['Duration'] == -1)) and ((data['IAT'] <= 166729152.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] > 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 3.07) or (data['flow_duration'] == -1)) and ((data['flow_duration'] <= 3.52) or (data['flow_duration'] == -1)) and ((data['Rate'] > 372.16) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'Spoofing', 66.67])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] <= 0.02) or (data['IAT'] == -1)) and ((data['AVG'] <= 55.42) or (data['AVG'] == -1)) and ((data['Radius'] <= 5.87) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number'], 'AVG': data['AVG'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] > 64.31) or (data['Max'] == -1)) and ((data['Max'] > 364.0) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] <= 14.65) or (data['urg_count'] == -1)) and ((data['Header_Length'] <= 180764.0) or (data['Header_Length'] == -1)) and ((data['ack_flag_number'] <= 0.5) or (data['ack_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'ack_flag_number': data['ack_flag_number']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] > 133481500.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 98.2) or (data['Tot_size'] == -1)) and ((data['syn_count'] > 1.7) or (data['syn_count'] == -1)) and ((data['Srate'] <= 73.62) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] > 0.02) or (data['ack_count'] == -1)) and ((data['Variance'] <= 0.64) or (data['Variance'] == -1)) and ((data['Min'] > 290.12) or (data['Min'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Variance': data['Variance'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] <= 11.14) or (data['Magnitue'] == -1)) and ((data['IAT'] <= 166850840.0) or (data['IAT'] == -1)) and ((data['Max'] <= 54.2) or (data['Max'] == -1)) and ((data['AVG'] <= 53.88) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Max': data['Max'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] <= 1398.8) or (data['Tot_sum'] == -1)) and ((data['syn_count'] <= 1.75) or (data['syn_count'] == -1)) and ((data['Protocol_Type'] > 10.7) or (data['Protocol_Type'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum'], 'Protocol_Type': data['Protocol_Type']}
        potential_paths.append([feature_dict, 'Recon', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)) and ((data['Rate'] > 292.85) or (data['Rate'] == -1)) and ((data['syn_count'] <= 0.45) or (data['syn_count'] == -1)) and ((data['AVG'] <= 1382.54) or (data['AVG'] == -1)) and ((data['Variance'] > 0.95) or (data['Variance'] == -1)) and ((data['syn_count'] > 0.25) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Rate': data['Rate'], 'syn_count': data['syn_count'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Brute_Force', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.39) or (data['flow_duration'] == -1)) and ((data['AVG'] <= 380.76) or (data['AVG'] == -1)) and ((data['Weight'] <= 77.83) or (data['Weight'] == -1)) and ((data['AVG'] <= 59.13) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'AVG': data['AVG'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'Brute_Force', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 188.85) or (data['urg_count'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] <= 6170.85) or (data['rst_count'] == -1)) and ((data['Tot_sum'] <= 435.1) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'BenignTraffic', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] > 56.38) or (data['Tot_size'] == -1)) and ((data['IAT'] <= 41462904.01) or (data['IAT'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['Radius'] > 8.31) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Brute_Force', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] > 60.5) or (data['Min'] == -1)) and ((data['SSH'] <= 0.5) or (data['SSH'] == -1)) and ((data['Covariance'] > 1.12) or (data['Covariance'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'SSH': data['SSH'], 'Covariance': data['Covariance'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'BenignTraffic', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] > 56.38) or (data['Tot_size'] == -1)) and ((data['IAT'] <= 41462904.01) or (data['IAT'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['Radius'] <= 8.31) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] <= 11.5) or (data['Number'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] > 64.31) or (data['Max'] == -1)) and ((data['Max'] <= 364.0) or (data['Max'] == -1)) and ((data['fin_count'] <= 0.32) or (data['fin_count'] == -1)) and ((data['IAT'] > 83165664.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'DDoS', 50.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] <= 203.92) or (data['AVG'] == -1)) and ((data['IAT'] <= 166850728.0) or (data['IAT'] == -1)) and ((data['Duration'] > 116.55) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] <= 0.02) or (data['IAT'] == -1)) and ((data['AVG'] <= 55.42) or (data['AVG'] == -1)) and ((data['Radius'] > 5.87) or (data['Radius'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number'], 'AVG': data['AVG'], 'Radius': data['Radius']}
        potential_paths.append([feature_dict, 'Recon', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] <= 0.02) or (data['IAT'] == -1)) and ((data['AVG'] > 55.42) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] > 203.92) or (data['AVG'] == -1)) and ((data['Header_Length'] > 7715.2) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 12.1) or (data['urg_count'] == -1)) and ((data['Max'] > 3076.5) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Spoofing', 50.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] > 0.02) or (data['IAT'] == -1)) and ((data['Number'] > 7.01) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] > 22.49) or (data['Srate'] == -1)) and ((data['syn_count'] <= 1.55) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.2) or (data['flow_duration'] == -1)) and ((data['Rate'] <= 1169.08) or (data['Rate'] == -1)) and ((data['fin_count'] > 0.35) or (data['fin_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'Rate': data['Rate'], 'fin_count': data['fin_count']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] <= 0.39) or (data['flow_duration'] == -1)) and ((data['AVG'] > 380.76) or (data['AVG'] == -1)) and ((data['Duration'] <= 61.5) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'AVG': data['AVG'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] <= 0.29) or (data['syn_count'] == -1)) and ((data['flow_duration'] > 0.39) or (data['flow_duration'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 6.0) or (data['Number'] == -1)) and ((data['Srate'] > 695.91) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'flow_duration': data['flow_duration'], 'TCP': data['TCP'], 'Number': data['Number'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Mirai', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] <= 140.4) or (data['Weight'] == -1)) and ((data['Protocol_Type'] <= 25.4) or (data['Protocol_Type'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['SSH'] > 0.5) or (data['SSH'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Protocol_Type': data['Protocol_Type'], 'HTTPS': data['HTTPS'], 'SSH': data['SSH']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] <= 9.28) or (data['Number'] == -1)) and ((data['IAT'] > 0.02) or (data['IAT'] == -1)) and ((data['Number'] <= 7.01) or (data['Number'] == -1)) and ((data['Tot_sum'] > 303.1) or (data['Tot_sum'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] > 56.38) or (data['Tot_size'] == -1)) and ((data['IAT'] <= 41462904.01) or (data['IAT'] == -1)) and ((data['IAT'] > 0.0) or (data['IAT'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] <= 82721.44) or (data['Header_Length'] == -1)) and ((data['Weight'] > 140.4) or (data['Weight'] == -1)) and ((data['Tot_sum'] <= 557.26) or (data['Tot_sum'] == -1)) and ((data['Srate'] > 107.41) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'Weight': data['Weight'], 'Tot_sum': data['Tot_sum'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'DoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] > 11.14) or (data['Magnitue'] == -1)) and ((data['Min'] > 52.0) or (data['Min'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] <= 11.14) or (data['Magnitue'] == -1)) and ((data['IAT'] > 166850840.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] <= 10.63) or (data['Magnitue'] == -1)) and ((data['Tot_size'] <= 56.38) or (data['Tot_size'] == -1)) and ((data['Number'] > 9.28) or (data['Number'] == -1)) and ((data['Number'] > 9.56) or (data['Number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'Tot_size': data['Tot_size'], 'Number': data['Number']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] > 193.08) or (data['Weight'] == -1)) and ((data['Magnitue'] > 11.14) or (data['Magnitue'] == -1)) and ((data['Min'] <= 52.0) or (data['Min'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Magnitue': data['Magnitue'], 'Min': data['Min']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] > 0.0) or (data['fin_count'] == -1)) and ((data['Weight'] <= 193.08) or (data['Weight'] == -1)) and ((data['fin_count'] <= 0.47) or (data['fin_count'] == -1)) and ((data['Max'] <= 64.31) or (data['Max'] == -1)) and ((data['AVG'] > 56.22) or (data['AVG'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'Weight': data['Weight'], 'Max': data['Max'], 'AVG': data['AVG']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] > 0.05) or (data['syn_count'] == -1)) and ((data['fin_count'] > 0.05) or (data['fin_count'] == -1)) and ((data['Tot_sum'] <= 1398.8) or (data['Tot_sum'] == -1)) and ((data['syn_count'] > 1.75) or (data['syn_count'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'fin_count': data['fin_count'], 'Tot_sum': data['Tot_sum']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['IAT'] <= 78690612.0) or (data['IAT'] == -1)) and ((data['Weight'] <= 83.68) or (data['Weight'] == -1)) and ((data['flow_duration'] <= 516.47) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Weight': data['Weight'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)) and ((data['Covariance'] <= 90.4) or (data['Covariance'] == -1)) and ((data['flow_duration'] > 38.82) or (data['flow_duration'] == -1)) and ((data['UDP'] <= 0.5) or (data['UDP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Covariance': data['Covariance'], 'flow_duration': data['flow_duration'], 'UDP': data['UDP']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)) and ((data['Covariance'] <= 90.4) or (data['Covariance'] == -1)) and ((data['flow_duration'] > 38.82) or (data['flow_duration'] == -1)) and ((data['UDP'] > 0.5) or (data['UDP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Covariance': data['Covariance'], 'flow_duration': data['flow_duration'], 'UDP': data['UDP']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] > 0.15) or (data['flow_duration'] == -1)) and ((data['rst_count'] > 287.0) or (data['rst_count'] == -1)) and ((data['syn_count'] > 0.7) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.0) or (data['IAT'] == -1)) and ((data['Magnitue'] > 53.6) or (data['Magnitue'] == -1)) and ((data['Header_Length'] <= 427410.41) or (data['Header_Length'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'syn_count': data['syn_count'], 'Magnitue': data['Magnitue'], 'Header_Length': data['Header_Length']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] > 133481500.0) or (data['IAT'] == -1)) and ((data['Tot_size'] <= 98.2) or (data['Tot_size'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Tot_size': data['Tot_size']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 188.85) or (data['urg_count'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] > 84.4) or (data['Duration'] == -1)) and ((data['Header_Length'] > 221395.0) or (data['Header_Length'] == -1)) and ((data['Radius'] <= 56.66) or (data['Radius'] == -1)) and ((data['Srate'] <= 34.16) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'Header_Length': data['Header_Length'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] > 0.39) or (data['Variance'] == -1)) and ((data['HTTPS'] <= 0.5) or (data['HTTPS'] == -1)) and ((data['Number'] <= 12.75) or (data['Number'] == -1)) and ((data['Max'] <= 466.88) or (data['Max'] == -1)) and ((data['Number'] > 7.5) or (data['Number'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)) and ((data['flow_duration'] <= 0.59) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'HTTPS': data['HTTPS'], 'Number': data['Number'], 'Max': data['Max'], 'HTTP': data['HTTP'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] <= 292.18) or (data['Tot_size'] == -1)) and ((data['Radius'] <= 5.41) or (data['Radius'] == -1)) and ((data['Tot_sum'] > 700.96) or (data['Tot_sum'] == -1)) and ((data['Magnitue'] <= 10.68) or (data['Magnitue'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Radius': data['Radius'], 'Tot_sum': data['Tot_sum'], 'Magnitue': data['Magnitue']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] > 188.85) or (data['urg_count'] == -1)) and ((data['HTTP'] <= 0.5) or (data['HTTP'] == -1)) and ((data['rst_count'] > 6170.85) or (data['rst_count'] == -1)) and ((data['psh_flag_number'] > 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'HTTP': data['HTTP'], 'rst_count': data['rst_count'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] <= 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['syn_count'] <= 0.05) or (data['syn_count'] == -1)) and ((data['Duration'] <= 84.4) or (data['Duration'] == -1)) and ((data['rst_count'] > 4.3) or (data['rst_count'] == -1)) and ((data['Tot_sum'] <= 1616.65) or (data['Tot_sum'] == -1)) and ((data['HTTP'] > 0.5) or (data['HTTP'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'syn_count': data['syn_count'], 'Duration': data['Duration'], 'rst_count': data['rst_count'], 'Tot_sum': data['Tot_sum'], 'HTTP': data['HTTP']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] <= 0.02) or (data['ack_count'] == -1)) and ((data['Tot_size'] > 292.18) or (data['Tot_size'] == -1)) and ((data['Tot_size'] > 902.01) or (data['Tot_size'] == -1)) and ((data['Duration'] <= 54.0) or (data['Duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Tot_size': data['Tot_size'], 'Duration': data['Duration']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] <= 0.5) or (data['TCP'] == -1)) and ((data['ack_count'] > 0.02) or (data['ack_count'] == -1)) and ((data['Variance'] > 0.64) or (data['Variance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'ack_count': data['ack_count'], 'Variance': data['Variance']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] <= 11.5) or (data['Number'] == -1)) and ((data['Number'] <= 7.5) or (data['Number'] == -1)) and ((data['HTTPS'] > 0.5) or (data['HTTPS'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'HTTPS': data['HTTPS']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 166602848.0) or (data['IAT'] == -1)) and ((data['Radius'] > 278.51) or (data['Radius'] == -1)) and ((data['IAT'] <= 167246344.0) or (data['IAT'] == -1)) and ((data['Srate'] <= 22.49) or (data['Srate'] == -1)) and ((data['AVG'] <= 203.92) or (data['AVG'] == -1)) and ((data['IAT'] <= 166850728.0) or (data['IAT'] == -1)) and ((data['Duration'] <= 116.55) or (data['Duration'] == -1)) and ((data['psh_flag_number'] > 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Radius': data['Radius'], 'Srate': data['Srate'], 'AVG': data['AVG'], 'Duration': data['Duration'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] <= 60.5) or (data['Min'] == -1)) and ((data['psh_flag_number'] > 0.5) or (data['psh_flag_number'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] > 0.5) or (data['rst_count'] == -1)) and ((data['flow_duration'] <= 0.15) or (data['flow_duration'] == -1)) and ((data['Weight'] <= 126.97) or (data['Weight'] == -1)) and ((data['Min'] <= 60.5) or (data['Min'] == -1)) and ((data['psh_flag_number'] <= 0.5) or (data['psh_flag_number'] == -1)) and ((data['Max'] > 80.8) or (data['Max'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'flow_duration': data['flow_duration'], 'Weight': data['Weight'], 'Min': data['Min'], 'psh_flag_number': data['psh_flag_number'], 'Max': data['Max']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] <= 83469472.0) or (data['IAT'] == -1)) and ((data['Header_Length'] > 82721.44) or (data['Header_Length'] == -1)) and ((data['urg_count'] <= 188.85) or (data['urg_count'] == -1)) and ((data['urg_count'] > 14.65) or (data['urg_count'] == -1)) and ((data['Tot_size'] > 2347.6) or (data['Tot_size'] == -1)) and ((data['Covariance'] > 915674.0) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Header_Length': data['Header_Length'], 'urg_count': data['urg_count'], 'Tot_size': data['Tot_size'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] > 83033340.0) or (data['IAT'] == -1)) and ((data['fin_count'] <= 0.0) or (data['fin_count'] == -1)) and ((data['TCP'] > 0.5) or (data['TCP'] == -1)) and ((data['Number'] > 11.5) or (data['Number'] == -1)) and ((data['Std'] > 0.38) or (data['Std'] == -1)) and ((data['Magnitue'] <= 11.12) or (data['Magnitue'] == -1)) and ((data['syn_flag_number'] <= 0.5) or (data['syn_flag_number'] == -1)) and ((data['IAT'] <= 166605808.0) or (data['IAT'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'fin_count': data['fin_count'], 'TCP': data['TCP'], 'Number': data['Number'], 'Magnitue': data['Magnitue'], 'syn_flag_number': data['syn_flag_number']}
        potential_paths.append([feature_dict, 'Brute_Force', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['IAT'] <= 78690612.0) or (data['IAT'] == -1)) and ((data['Weight'] > 83.68) or (data['Weight'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Weight': data['Weight']}
        potential_paths.append([feature_dict, 'DDoS', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] > 0.01) or (data['IAT'] == -1)) and ((data['IAT'] <= 78690612.0) or (data['IAT'] == -1)) and ((data['Weight'] <= 83.68) or (data['Weight'] == -1)) and ((data['flow_duration'] > 516.47) or (data['flow_duration'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Weight': data['Weight'], 'flow_duration': data['flow_duration']}
        potential_paths.append([feature_dict, 'Spoofing', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] > 133481500.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 98.2) or (data['Tot_size'] == -1)) and ((data['syn_count'] <= 1.7) or (data['syn_count'] == -1)) and ((data['Rate'] <= 74.44) or (data['Rate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count'], 'Rate': data['Rate']}
        potential_paths.append([feature_dict, 'BenignTraffic', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)) and ((data['Covariance'] > 90.4) or (data['Covariance'] == -1)) and ((data['Covariance'] > 97.33) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    if ((data['Std'] <= 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 83033340.0) or (data['IAT'] == -1)) and ((data['rst_count'] <= 0.5) or (data['rst_count'] == -1)) and ((data['Magnitue'] > 10.63) or (data['Magnitue'] == -1)) and ((data['syn_count'] > 0.29) or (data['syn_count'] == -1)) and ((data['IAT'] <= 0.01) or (data['IAT'] == -1)) and ((data['Covariance'] > 90.4) or (data['Covariance'] == -1)) and ((data['Covariance'] <= 97.33) or (data['Covariance'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'rst_count': data['rst_count'], 'Magnitue': data['Magnitue'], 'syn_count': data['syn_count'], 'Covariance': data['Covariance']}
        potential_paths.append([feature_dict, 'Web-Based', 100.0])
    if ((data['Std'] > 9.8) or (data['Std'] == -1)) and ((data['IAT'] <= 166602848.0) or (data['IAT'] == -1)) and ((data['Variance'] <= 0.39) or (data['Variance'] == -1)) and ((data['IAT'] > 83469472.0) or (data['IAT'] == -1)) and ((data['IAT'] > 133481500.0) or (data['IAT'] == -1)) and ((data['Tot_size'] > 98.2) or (data['Tot_size'] == -1)) and ((data['syn_count'] > 1.7) or (data['syn_count'] == -1)) and ((data['Srate'] > 73.62) or (data['Srate'] == -1)):
        feature_dict = {'Std': data['Std'], 'IAT': data['IAT'], 'Variance': data['Variance'], 'Tot_size': data['Tot_size'], 'syn_count': data['syn_count'], 'Srate': data['Srate']}
        potential_paths.append([feature_dict, 'Recon', 100.0])
    all_entries_res.append(potential_paths)
    return None


In [10]:
for index, row in df.iterrows():
    selected_features = random.sample(all_features, 1)
    
    for feature in selected_features:
        df.at[index, feature] = -1
    if df.at[index, "fin_flag_number"] == -1:
        df.at[index, "fin_count"] = -1
    if df.at[index, "syn_flag_number"] == -1:
        df.at[index, "syn_count"] = -1
    if df.at[index, "rst_flag_number"] == -1:
        df.at[index, "rst_count"] = -1
    if df.at[index, "ack_flag_number"] == -1:
        df.at[index, "ack_count"] = -1

In [11]:
df.head()

flow_duration  Header_Length  Protocol_Type  Duration        Rate       Srate  Drate  fin_flag_number  syn_flag_number  rst_flag_number  psh_flag_number  ack_flag_number  ece_flag_number  cwr_flag_number  ack_count  syn_count  fin_count  urg_count  rst_count  HTTP  HTTPS  DNS  Telnet  SMTP  SSH  IRC  TCP  UDP  DHCP  ARP  ICMP  IPv  LLC  Tot_sum     Min     Max          AVG         Std  Tot_size           IAT  Number   Magnitue       Radius     Covariance  Variance  Weight          label
447      13.215984       863491.0            6.0     232.0   62.537910   62.537910    0.0              0.0              0.0             -1.0              0.0              1.0              0.0              0.0        0.0        0.0        0.0       32.0       -1.0   0.0    1.0  0.0     0.0   0.0  0.0  0.0  1.0  0.0   0.0  0.0   0.0  1.0  1.0   2029.0    66.0  1072.0   133.278403  249.988643      66.0  1.665182e+08    13.5  16.324726   354.298748   63225.672546       1.0   244.6  BenignTraffic
485     122.479718        62172.8           13.7      63.6    5.057926    5.057926    0.0              0.0              0.0              0.0              0.0              0.0              0.0              0.0        0.0       -1.0        0.0      172.8      351.2   0.0    0.0  0.0     0.0   0.0  0.0  0.0  0.0  1.0   0.0  0.0   0.0  1.0  1.0   1101.9    50.0   230.0    71.085046   45.831857      68.1  1.665238e+08    13.5  11.920195    64.970328    2114.415628       1.0   244.6  BenignTraffic
215      17.803338           -1.0            7.1      83.1   81.390655   81.390655    0.0              0.0              0.0              0.0              0.0              1.0              0.0              0.0        0.0        1.6        0.0       79.2      838.8   0.0    1.0  0.0     0.0   0.0  0.0  0.0  1.0  0.0   0.0  0.0   0.0  1.0  1.0  17328.5    54.0  2817.2  1105.553872  827.989774    1441.5  1.665213e+08    13.5  47.082245  1170.507395  688084.298393       1.0   244.6  BenignTraffic
212      24.131660      1738870.0            6.0      64.0   70.136075   70.136075    0.0              0.0              0.0              0.0              0.0              1.0              0.0              0.0        0.0        2.0        0.0       64.1     1691.5   0.0    1.0  0.0     0.0   0.0  0.0  0.0  1.0  0.0   0.0  0.0   0.0  1.0  1.0  10183.0  1487.6  2672.4  1811.762540  505.204813    1777.2 -1.000000e+00     5.5  60.131155   714.467498  320093.330391       0.8    38.5  BenignTraffic
480       1.622064       575018.0            6.0     232.0  316.569854  316.569854    0.0              0.0              0.0              0.0              0.0              1.0              0.0              0.0        0.0        2.0        0.0       17.0      512.5   0.0    1.0  0.0     0.0   0.0  0.0  0.0  1.0  0.0   0.0  0.0   0.0  1.0  1.0    363.0    66.0    66.0    66.000000   -1.000000      66.0  1.104093e-03     5.5  11.489125     0.000000       0.000000       0.0    38.5  BenignTraffic

In [12]:
df.to_csv('../missing_feature/1_missing/dt_1_1missing_features.csv', index=False)

In [13]:
all_entries_res = []

In [14]:
df.apply(lambda row: classify(row), axis=1)

447     None
485     None
215     None
212     None
480     None
515     None
163     None
77      None
527     None
145     None
265     None
31      None
55      None
90      None
557     None
76      None
2       None
368     None
395     None
286     None
131     None
148     None
49      None
621     None
437     None
110     None
257     None
578     None
620     None
256     None
334     None
261     None
184     None
554     None
132     None
487     None
335     None
612     None
181     None
599     None
381     None
39      None
86      None
608     None
318     None
208     None
260     None
513     None
78      None
344     None
556     None
281     None
10      None
259     None
600     None
311     None
135     None
434     None
210     None
30      None
579     None
482     None
192     None
509     None
588     None
300     None
56      None
196     None
535     None
235     None
272     None
24      None
82      None
158     None
543     None
220     None
592     None

In [15]:
count = 1
for sublist in all_entries_res:
    for list in sublist:
        entry = list[0]
        # print(str(entry) + "  " + str(list[1]) + "   " + str(list[2]))
        if all(value == -1 for value in entry.values()):
            print("All values in this dictionary are -1.")
            print(count)
    count +=1
    # print("\n\n")

In [16]:
for sublist in all_entries_res:
    # Check if the sublist has at least two elements
    if len(sublist) >= 2:
        # Check if all lists in the sublist are the same (some cases use the same features set to determine and result are the same, however the threshold values could be different. But
        # it looks use the same paths, but indeed it is not)
        if all(sublist[0] == lst for lst in sublist):
            print("All lists in this sublist are the same:", sublist)

All lists in this sublist are the same: [[{'Std': 359.8246073324695, 'IAT': 167638861.8192147, 'Radius': -1.0}, 'Web-Based', 100.0], [{'Std': 359.8246073324695, 'IAT': 167638861.8192147, 'Radius': -1.0}, 'Web-Based', 100.0]]


In [17]:
#used when value is zero
feature_descriptions_zero = {
    'ts': "Timestamp",
    'flow_duration': "The Duration of the packet's flow",
    'Header_Length': "Packet header length",
    'Protocol_Type': "Protocol type",
    'Duration': "Time-to-Live",
    'Rate': "Rate of packet transmission",
    'Srate': "Rate of outbound packets transmission",
    'Drate': "Rate of inbound packets transmission",
    'fin_flag_number': "Count of FIN flags (which signal the end of data transmission)",
    'syn_flag_number': "Count of SYN flags (indicating the initiation of a TCP three-way handshake)",
    'rst_flag_number': "Count of RST flags (used for resetting connections)",
    'psh_flag_number': "Count of PSH flags (instructing to push buffered data to the receiving application)",
    'ack_flag_number': "Count of ACK flags (used to acknowledge packet receipts)",
    'ece_flag_number': "Count of ECE flags (indicating network congestion)",
    'cwr_flag_number': "Count of CWR flags (signaling reduced transmission rate due to congestion notification)",
    'ack_count': "Number of packets with an ACK flag",
    'syn_count': "Number of packets with a SYN flag",
    'fin_count': "Number of packets with a FIN flag",
    'urg_count': "Number of packets with an URG flag",
    'rst_count': "Number of packets with an RST flag",
    'HTTP': "Application layer protocol is HTTP",
    'HTTPS': "Application layer protocol is HTTPS",
    'DNS': "Application layer protocol is DNS",
    'Telnet': "Application layer protocol is Telnet",
    'SMTP': "Application layer protocol is SMTP",
    'SSH': "Application layer protocol is SSH",
    'IRC': "Application layer protocol is IRC",
    'TCP': "Transport layer protocol is TCP",
    'UDP': "Transport layer protocol is UDP",
    'DHCP': "Application layer protocol is DHCP",
    'ARP': "Link layer protocol is ARP",
    'ICMP': "Network layer protocol is ICMP",
    'IPv': "Network layer protocol is IP",
    'LLC': "Link layer protocol is LLC",
    'Tot_sum': "Total sum of packets lengths",
    'Min': "Minimum packet length in the flow",
    'Max': "Maximum packet length in the flow",
    'AVG': "Average packet length in the flow",
    'Std': "Standard deviation of packet length",
    'Tot_size': "Packet's length",
    'IAT': "The time difference between two consecutive packets",
    'Number': "The total number of packets",
    'Magnitue': "Magnitude (calculated as the mean of the average lengths of incoming and outgoing packets in the flow)",
    'Radius': "Radius (calculated as the averaged variances of packet lengths for incoming and outgoing packets)",
    'Covariance': "Covariance (coveriance of the lengths of incoming and outgoing packets)",
    'Variance': "Variance (calculated as the ratio of variances in packet lengths between incoming and outgoing packets)",
    'Weight': "Weight (calculated as the product of the counts of incoming and outgoing packets)"
}

feature_descriptions = {
    'ts': "Timestamp",
    'flow_duration': "On a scale from Level 1 to Level 12, the Duration of the packet's flow",
    'Header_Length': "On a scale from Level 1 to Level 12, Packet header length",
    'Protocol_Type': "Protocol type",
    'Duration': "On a scale from Level 1 to Level 10, Time-to-Live",
    'Rate': "On a scale from Level 1 to Level 11, Rate of packet transmission",
    'Srate': "On a scale from Level 1 to Level 9, Rate of outbound packets transmission",
    'Drate': "Rate of inbound packets transmission",
    'fin_flag_number': "Count of FIN flags (which signal the end of data transmission)",
    'syn_flag_number': "Count of SYN flags (indicating the initiation of a TCP three-way handshake)",
    'rst_flag_number': "Count of RST flags (used for resetting connections)",
    'psh_flag_number': "Count of PSH flags (instructing to push buffered data to the receiving application)",
    'ack_flag_number': "Count of ACK flags (used to acknowledge packet receipts)",
    'ece_flag_number': "Count of ECE flags (indicating network congestion)",
    'cwr_flag_number': "Count of CWR flags (signaling reduced transmission rate due to congestion notification)",
    'ack_count': "Number of packets with an ACK flag",
    'syn_count': "On a scale from Level 1 to Level 12, Number of packets with a SYN flag",
    'fin_count': "Number of packets with a FIN flag",
    'urg_count': "On a scale from Level 1 to Level 8, Number of packets with an URG flag",
    'rst_count': "On a scale from Level 1 to Level 15, number of packets with an RST flag",
    'HTTP': "Application layer protocol is HTTP",
    'HTTPS': "Application layer protocol is HTTPS",
    'DNS': "Application layer protocol is DNS",
    'Telnet': "Application layer protocol is Telnet",
    'SMTP': "Application layer protocol is SMTP",
    'SSH': "Application layer protocol is SSH",
    'IRC': "Application layer protocol is IRC",
    'TCP': "Transport layer protocol is TCP",
    'UDP': "Transport layer protocol is UDP",
    'DHCP': "Application layer protocol is DHCP",
    'ARP': "Link layer protocol is ARP",
    'ICMP': "Network layer protocol is ICMP",
    'IPv': "Network layer protocol is IP",
    'LLC': "Link layer protocol is LLC",
    'Tot_sum': "On a scale from Level 1 to Level 11, Total sum of packets lengths",
    'Min': "On a scale from Level 1 to Level 8, Minimum packet length in the flow",
    'Max': "On a scale from Level 1 to Level 12, Maximum packet length in the flow",
    'AVG': "On a scale from Level 1 to Level 11, average packet length in the flow",
    'Std': "Standard deviation of packet length",
    'Tot_size': "On a scale from Level 1 to Level 10, Packet's length",
    'IAT': "The time difference between two consecutive packets",
    'Number': "On a scale from Level 1 to Level 9, the total number of packets",
    'Magnitue': "On a scale from Level 1 to Level 8, Magnitude (calculated as the mean of the average lengths of incoming and outgoing packets in the flow)",
    'Radius': "On a scale from Level 1 to Level 10, Radius (calculated as the averaged variances of packet lengths for incoming and outgoing packets)",
    'Covariance': "On a scale from Level 1 to Level 13, Covariance (coveriance of the lengths of incoming and outgoing packets)",
    'Variance': "Variance (calculated as the ratio of variances in packet lengths between incoming and outgoing packets)",
    'Weight': "On a scale from Level 1 to Level 8, Weight (calculated as the product of the counts of incoming and outgoing packets)"
}

In [18]:
layer_features_unknown = {
    'HTTP': "Application layer protocol is unknown",
    'HTTPS': "Application layer protocol is unknown",
    'DNS': "Application layer protocol is unknown",
    'Telnet': "Application layer protocol is unknown",
    'SMTP': "Application layer protocol is unknown",
    'SSH': "Application layer protocol is unknown",
    'IRC': "Application layer protocol is unknown",
    'TCP': "Transport layer protocol is unknown",
    'UDP': "Transport layer protocol is unknown",
    'DHCP': "Application layer protocol is unknown",
    'ARP': "Link layer protocol is unknown",
    'ICMP': "Network layer protocol is unknown",
    'IPv': "Network layer protocol is unknown",
    'LLC': "Link layer protocol is unknown",
}

In [19]:
def create_description(row):
    descriptions = []
    # for numerical feature
    for feature in numerical_features:
        value = row.get(feature)
        if pd.notnull(value):  # Check if the feature is not NaN
            if value == "unknown":
                descriptions.append(f"{feature_descriptions_zero.get(feature, feature)} is {value}.")
            elif value == "zero":
                descriptions.append(f"{feature_descriptions_zero.get(feature, feature)} is {value}.")
            else:
                descriptions.append(f"{feature_descriptions.get(feature, feature)} is {value}.")
            
    # flag
    for feature in flag_features:
        if row.get(feature) == -1:
            descriptions.append(f"{layer_features_unknown.get(feature, feature)}.")
        elif row.get(feature) == 1:
            protocol_name = ' '.join(feature.split('_')).capitalize()
            descriptions.append(f"{feature_descriptions.get(feature, feature)}.")
            
    if pd.notnull(row.get("psh_flag_number")):
        value = row.get("psh_flag_number")
        if value == -1:
            descriptions.append("The existance of psh(push) flag is unknown")
        elif value == 1:
            descriptions.append("The psh(push) flag exists in this traffic")
            
    if pd.notnull(row.get("rst_flag_number")):
        value = row.get("rst_flag_number")
        rst_count = row.get("rst_count")
        if value == -1:
            descriptions.append("The existance of rst(reset) flag is unknown")
        elif value == 1 and rst_count != "zero":
            descriptions.append("The rst(reset) flag exists in this traffic")
            
    if pd.notnull(row.get("ack_flag_number")):
        value = row.get("ack_flag_number")
        ack_count = row.get("ack_count")
        if value == -1:
            descriptions.append("The existance of ack(Acknowledgment) flag is unknown")
        elif value == 1 and ack_count != "zero":
            descriptions.append("The ack(Acknowledgment) flag exists in this traffic")
            
    if pd.notnull(row.get("syn_flag_number")):
        value = row.get("syn_flag_number")
        syn_count = row.get("syn_count")
        if value == -1:
            descriptions.append("The existance of syn(Synchronize) flag is unknown")
        elif value == 1 and syn_count != "zero":
            descriptions.append("The syn(Synchronize) flag exists in this traffic")

    return ' '.join(descriptions)

In [20]:
def categorize_std(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.38:
        return 'low'
    elif value <= 9.8:
        return 'medium'
    else:
        return 'high'

def categorize_rst_count(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.5:
        return 'level 1'
    elif value <= 1.32:
        return 'level 2'
    elif value <= 4.3:
        return 'level 3'
    elif value <= 5.44:
        return 'level 4'
    elif value <= 39.4:
        return 'level 5'
    elif value <= 89.1:
        return 'level 6'
    elif value <= 115.55:
        return 'level 7'
    elif value <= 178.75:
        return 'level 8'
    elif value <= 240.9:
        return 'level 9'
    elif value <= 284.45:
        return 'level 10'
    elif value <= 287.0:
        return 'level 11'
    elif value <= 732.1:
        return 'level 12'
    elif value <= 1266.6:
        return 'level 13'
    elif value <= 6170.85:
        return 'level 14'
    else:
        return 'level 15'
    
def categorize_magnitude(value):
    if value == 0.0:
        return 'zero'
    elif value <= 10.39:
        return 'level 1'
    elif value <= 10.63:
        return 'level 2'
    elif value <= 10.68:
        return 'level 3'
    elif value <= 11.04:
        return 'level 4'
    elif value <= 11.12:
        return 'level 5'
    elif value <= 11.14:
        return 'level 6'
    elif value <= 53.6:
        return 'level 7'
    else:
        return 'level 8'

def categorize_tot_size(value):
    if value == 0.0:
        return 'zero'
    elif value <= 56.38:
        return 'level 1'
    elif value <= 66.45:
        return 'level 2'
    elif value <= 85.75:
        return 'level 3'
    elif value <= 98.2:
        return 'level 4'
    elif value <= 292.18:
        return 'level 5'
    elif value <= 350.8:
        return 'level 6'
    elif value <= 478.82:
        return 'level 7'
    elif value <= 902.01:
        return 'level 8'
    elif value <= 2347.6:
        return 'level 9'
    else:
        return 'level 10'

def categorize_number(value):
    if value == 0.0:
        return 'zero'
    elif value <= 6.0:
        return 'level 1'
    elif value <= 7.01:
        return 'level 2'
    elif value <= 7.5:
        return 'level 3'
    elif value <= 9.28:
        return 'level 4'
    elif value <= 9.5:
        return 'level 5'
    elif value <= 9.56:
        return 'level 6'
    elif value <= 11.5:
        return 'level 7'
    elif value <= 12.75:
        return 'level 8'
    else:
        return 'level 9'

def categorize_avg(value):
    if value == 0.0:
        return 'zero'
    elif value <= 53.88:
        return 'level 1'
    elif value <= 55.42:
        return 'level 2'
    elif value <= 56.22:
        return 'level 3'
    elif value <= 59.13:
        return 'level 4'
    elif value <= 60.58:
        return 'level 5'
    elif value <= 66.04:
        return 'level 6'
    elif value <= 98.91:
        return 'level 7'
    elif value <= 203.92:
        return 'level 8'
    elif value <= 380.76:
        return 'level 9'
    elif value <= 1382.54:
        return 'level 10'
    else:
        return 'level 11'

def categorize_radius(value):
    if value == 0.0:
        return 'zero'
    elif value <= 5.41:
        return 'level 1'
    elif value <= 5.87:
        return 'level 2'
    elif value <= 8.31:
        return 'level 3'
    elif value <= 48.07:
        return 'level 4'
    elif value <= 56.66:
        return 'level 5'
    elif value <= 69.8:
        return 'level 6'
    elif value <= 81.55:
        return 'level 7'
    elif value <= 278.51:
        return 'level 8'
    elif value <= 753.63:
        return 'level 9'
    else:
        return 'level 10'

def categorize_tot_sum(value):
    if value == 0.0:
        return 'zero'
    elif value <= 303.1:
        return 'level 1'
    elif value <= 354.75:
        return 'level 2'
    elif value <= 435.1:
        return 'level 3'
    elif value <= 442.75:
        return 'level 4'
    elif value <= 557.26:
        return 'level 5'
    elif value <= 700.96:
        return 'level 6'
    elif value <= 1398.8:
        return 'level 7'
    elif value <= 1616.65:
        return 'level 8'
    elif value <= 3884.2:
        return 'level 9'
    elif value <= 37934.4:
        return 'level 10'
    else:
        return 'level 11'

def categorize_syn_count(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.05:
        return 'level 1'
    elif value <= 0.1:
        return 'level 2'
    elif value <= 0.15:
        return 'level 3'
    elif value <= 0.25:
        return 'level 4'
    elif value <= 0.29:
        return 'level 5'
    elif value <= 0.45:
        return 'level 6'
    elif value <= 0.65:
        return 'level 7'
    elif value <= 0.7:
        return 'level 8'
    elif value <= 1.55:
        return 'level 9'
    elif value <= 1.7:
        return 'level 10'
    elif value <= 1.75:
        return 'level 11'
    else:
        return 'level 12'

def categorize_flow_duration(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.15:
        return 'level 1'
    elif value <= 0.2:
        return 'level 2'
    elif value <= 0.39:
        return 'level 3'
    elif value <= 0.59:
        return 'level 4'
    elif value <= 3.07:
        return 'level 5'
    elif value <= 3.52:
        return 'level 6'
    elif value <= 17.93:
        return 'level 7'
    elif value <= 20.54:
        return 'level 8'
    elif value <= 38.82:
        return 'level 9'
    elif value <= 72.36:
        return 'level 10'
    elif value <= 516.47:
        return 'level 11'
    else:
        return 'level 12'

def categorize_weight(value):
    if value == 0.0:
        return 'zero'
    elif value <= 77.83:
        return 'level 1'
    elif value <= 79.94:
        return 'level 2'
    elif value <= 83.68:
        return 'level 3'
    elif value <= 90.03:
        return 'level 4'
    elif value <= 126.97:
        return 'level 5'
    elif value <= 140.4:
        return 'level 6'
    elif value <= 193.08:
        return 'level 7'
    else:
        return 'level 8'

def categorize_duration(value):
    if value == 0.0:
        return 'zero'
    elif value <= 54.0:
        return 'level 1'
    elif value <= 57.0:
        return 'level 2'
    elif value <= 61.5:
        return 'level 3'
    elif value <= 62.75:
        return 'level 4'
    elif value <= 84.4:
        return 'level 5'
    elif value <= 100.6:
        return 'level 6'
    elif value <= 116.55:
        return 'level 7'
    elif value <= 160.4:
        return 'level 8'
    elif value <= 246.5:
        return 'level 9'
    else:
        return 'level 10'

def categorize_srate(value):
    if value == 0.0:
        return 'zero'
    elif value <= 1.34:
        return 'level 1'
    elif value <= 6.95:
        return 'level 2'
    elif value <= 22.49:
        return 'level 3'
    elif value <= 29.92:
        return 'level 4'
    elif value <= 34.16:
        return 'level 5'
    elif value <= 73.62:
        return 'level 6'
    elif value <= 107.41:
        return 'level 7'
    elif value <= 695.91:
        return 'level 8'
    else:
        return 'level 9'

def categorize_covariance(value):
    if value == 0.0:
        return 'zero'
    elif value <= 1.12:
        return 'level 1'
    elif value <= 90.4:
        return 'level 2'
    elif value <= 97.33:
        return 'level 3'
    elif value <= 4959.5:
        return 'level 4'
    elif value <= 6269.43:
        return 'level 5'
    elif value <= 18379.3:
        return 'level 6'
    elif value <= 19281.41:
        return 'level 7'
    elif value <= 81486.11:
        return 'level 8'
    elif value <= 86125.98:
        return 'level 9'
    elif value <= 915674.0:
        return 'level 10'
    elif value <= 1051078.34:
        return 'level 11'
    elif value <= 2317899.75:
        return 'level 12'
    else:
        return 'level 13'

def categorize_min(value):
    if value == 0.0:
        return 'zero'
    elif value <= 52.0:
        return 'level 1'
    elif value <= 60.5:
        return 'level 2'
    elif value <= 67.7:
        return 'level 3'
    elif value <= 67.95:
        return 'level 4'
    elif value <= 290.12:
        return 'level 5'
    elif value <= 786.0:
        return 'level 6'
    elif value <= 1504.0:
        return 'level 7'
    else:
        return 'level 8'

def categorize_max(value):
    if value == 0.0:
        return 'zero'
    elif value <= 54.2:
        return 'level 1'
    elif value <= 64.31:
        return 'level 2'
    elif value <= 74.7:
        return 'level 3'
    elif value <= 80.8:
        return 'level 4'
    elif value <= 90.5:
        return 'level 5'
    elif value <= 140.5:
        return 'level 6'
    elif value <= 364.0:
        return 'level 7'
    elif value <= 466.88:
        return 'level 8'
    elif value <= 873.25:
        return 'level 9'
    elif value <= 3076.5:
        return 'level 10'
    elif value <= 3093.8:
        return 'level 11'
    else:
        return 'level 12'

def categorize_header_length(value):
    if value == 0.0:
        return 'zero'
    elif value <= 7715.2:
        return 'level 1'
    elif value <= 23286.3:
        return 'level 2'
    elif value <= 27577.7:
        return 'level 3'
    elif value <= 82721.44:
        return 'level 4'
    elif value <= 150021.5:
        return 'level 5'
    elif value <= 156572.95:
        return 'level 6'
    elif value <= 180764.0:
        return 'level 7'
    elif value <= 220049.1:
        return 'level 8'
    elif value <= 221395.0:
        return 'level 9'
    elif value <= 427410.41:
        return 'level 10'
    elif value <= 1000736.09:
        return 'level 11'
    else:
        return 'level 12'

def categorize_rate(value):
    if value == 0.0:
        return 'zero'
    elif value <= 3.37:
        return 'level 1'
    elif value <= 7.23:
        return 'level 2'
    elif value <= 25.51:
        return 'level 3'
    elif value <= 28.62:
        return 'level 4'
    elif value <= 74.44:
        return 'level 5'
    elif value <= 106.78:
        return 'level 6'
    elif value <= 114.73:
        return 'level 7'
    elif value <= 292.85:
        return 'level 8'
    elif value <= 372.16:
        return 'level 9'
    elif value <= 1169.08:
        return 'level 10'
    else:
        return 'level 11'

def categorize_urg_count(value):
    if value == 0.0:
        return 'zero'
    elif value <= 12.1:
        return 'level 1'
    elif value <= 14.65:
        return 'level 2'
    elif value <= 36.65:
        return 'level 3'
    elif value <= 64.35:
        return 'level 4'
    elif value <= 86.1:
        return 'level 5'
    elif value <= 188.85:
        return 'level 6'
    elif value <= 340.9:
        return 'level 7'
    else:
        return 'level 8'

def categorize_fin_count(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.05:
        return 'extremely low'
    elif value <= 0.08:
        return 'low'
    elif value <= 0.32:
        return 'midly low'
    elif value <= 0.35:
        return 'midly high'
    elif value <= 0.47:
        return 'high'
    else:
        return 'extremely high'

def categorize_ack_count(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.02:
        return 'low'
    elif value <= 0.13:
        return 'medium'
    else:
        return 'high'

def categorize_variance(value):
    if value == 0.0:
        return 'zero'
    elif value <= 0.39:
        return 'extremely low'
    elif value <= 0.64:
        return 'low'
    elif value <= 0.83:
        return 'midly low'
    elif value <= 0.95:
        return 'midly high'
    elif value <= 0.97:
        return 'high'
    else:
        return 'extremely high'

def categorize_iat(value):
    if value == 0.0:
        return 'zero'
    if value <= 0.02:
        return 'extremely low'
    if value <= 41462904.01:
        return 'low'
    if value <= 78690612.0:
        return 'midly low'
    if value <= 83469472.0:
        return 'medium'
    if value <= 133481500.0:
        return 'midly high'
    if value <= 167246344.0:
        return 'high' 
    else:
        return 'extremely high'

In [21]:
def serialize_prediction_path(dict):
    if 'Std' in dict:
        if dict['Std'] == -1:
            dict['Std'] = "unknown"
        else:
            dict['Std'] = categorize_std(dict['Std'])
    
    if 'IAT' in dict:
        if dict['IAT'] == -1:
            dict['IAT'] = "unknown"
        else:
            dict['IAT'] = categorize_iat(dict['IAT'])
    
    if 'rst_count' in dict:
        if dict['rst_count'] == -1:
            dict['rst_count'] = "unknown"
        else:
            dict['rst_count'] = categorize_rst_count(dict['rst_count'])
    
    if 'Magnitue' in dict:
        if dict['Magnitue'] == -1:
            dict['Magnitue'] = "unknown"
        else:
            dict['Magnitue'] = categorize_magnitude(dict['Magnitue'])
    
    if 'Tot_size' in dict:
        if dict['Tot_size'] == -1:
            dict['Tot_size'] = "unknown"
        else:
            dict['Tot_size'] = categorize_tot_size(dict['Tot_size'])
    
    if 'Number' in dict:
        if dict['Number'] == -1:
            dict['Number'] = "unknown"
        else:
            dict['Number'] = categorize_number(dict['Number'])
    
    if 'AVG' in dict:
        if dict['AVG'] == -1:
            dict['AVG'] = "unknown"
        else:
            dict['AVG'] = categorize_avg(dict['AVG'])
    
    if 'Radius' in dict:
        if dict['Radius'] == -1:
            dict['Radius'] = "unknown"
        else:
            dict['Radius'] = categorize_radius(dict['Radius'])
    
    if 'Tot_sum' in dict:
        if dict['Tot_sum'] == -1:
            dict['Tot_sum'] = "unknown"
        else:
            dict['Tot_sum'] = categorize_tot_sum(dict['Tot_sum'])
    
    if 'syn_count' in dict:
        if dict['syn_count'] == -1:
            dict['syn_count'] = "unknown"
        else:
            dict['syn_count'] = categorize_syn_count(dict['syn_count'])
    
    if 'flow_duration' in dict:
        if dict['flow_duration'] == -1:
            dict['flow_duration'] = "unknown"
        else:
            dict['flow_duration'] = categorize_flow_duration(dict['flow_duration'])
    
    if 'Weight' in dict:
        if dict['Weight'] == -1:
            dict['Weight'] = "unknown"
        else:
            dict['Weight'] = categorize_weight(dict['Weight'])
    
    if 'Duration' in dict:
        if dict['Duration'] == -1:
            dict['Duration'] = "unknown"
        else:
            dict['Duration'] = categorize_duration(dict['Duration'])
    
    if 'Srate' in dict:
        if dict['Srate'] == -1:
            dict['Srate'] = "unknown"
        else:
            dict['Srate'] = categorize_srate(dict['Srate'])
    
    if 'Covariance' in dict:
        if dict['Covariance'] == -1:
            dict['Covariance'] = "unknown"
        else:
            dict['Covariance'] = categorize_covariance(dict['Covariance'])
    
    if 'Min' in dict:
        if dict['Min'] == -1:
            dict['Min'] = "unknown"
        else:
            dict['Min'] = categorize_min(dict['Min'])
    
    if 'Max' in dict:
        if dict['Max'] == -1:
            dict['Max'] = "unknown"
        else:
            dict['Max'] = categorize_max(dict['Max'])
    
    if 'Header_Length' in dict:
        if dict['Header_Length'] == -1:
            dict['Header_Length'] = "unknown"
        else:
            dict['Header_Length'] = categorize_header_length(dict['Header_Length'])
    
    if 'Rate' in dict:
        if dict['Rate'] == -1:
            dict['Rate'] = "unknown"
        else:
            dict['Rate'] = categorize_rate(dict['Rate'])
    
    if 'urg_count' in dict:
        if dict['urg_count'] == -1:
            dict['urg_count'] = "unknown"
        else:
            dict['urg_count'] = categorize_urg_count(dict['urg_count'])
    
    if 'fin_count' in dict:
        if dict['fin_count'] == -1:
            dict['fin_count'] = "unknown"
        else:
            dict['fin_count'] = categorize_fin_count(dict['fin_count'])
    
    if 'ack_count' in dict:
        if dict['ack_count'] == -1:
            dict['ack_count'] = "unknown"
        else:
            dict['ack_count'] = categorize_ack_count(dict['ack_count'])
    
    if 'Variance' in dict:
        if dict['Variance'] == -1:
            dict['Variance'] = "unknown"
        else:
            dict['Variance'] = categorize_variance(dict['Variance'])
    
    if 'Protocol_Type' in dict:
        dict.pop('Protocol_Type')
        
    return create_description(dict)

In [22]:
for sublist in all_entries_res:
    for list in sublist:
        description = serialize_prediction_path(list[0])
        list.append(description)
        entry = list[0]
        print(str(entry) + "  " + str(list[1]) + "   " + str(list[2]) + "   " + str(list[3]))
        if all(value == -1 for value in entry.values()):
            print("All values in this dictionary are -1.")
    print("\n\n")

{'Std': 'high', 'IAT': 'high', 'Variance': 'extremely high', 'HTTPS': 1.0, 'Rate': 'level 5', 'rst_count': 'unknown', 'Covariance': 'level 8', 'Min': 'level 3', 'Weight': 'level 8'}  BenignTraffic   81.16   On a scale from Level 1 to Level 11, Rate of packet transmission is level 5. Number of packets with an RST flag is unknown. On a scale from Level 1 to Level 8, Minimum packet length in the flow is level 3. Standard deviation of packet length is high. The time difference between two consecutive packets is high. On a scale from Level 1 to Level 13, Covariance (coveriance of the lengths of incoming and outgoing packets) is level 8. Variance (calculated as the ratio of variances in packet lengths between incoming and outgoing packets) is extremely high. On a scale from Level 1 to Level 8, Weight (calculated as the product of the counts of incoming and outgoing packets) is level 8. Application layer protocol is HTTPS.
{'Std': 'high', 'IAT': 'high', 'Variance': 'extremely high', 'HTTPS': 

In [23]:
final_list = []

In [24]:
len_list = []

In [25]:
with open('../prob_files/prob_1_5000.json', 'r') as f:
    prob_dict = json.load(f)

In [26]:
idx = 0

In [27]:
for sublist in all_entries_res:
    #correct_label = sublist_1[0][1]
    correct_label = df.iloc[idx]["label"]
    idx += 1
    all_paths = []
    for list in sublist:
        all_unknown = False
        prob = None
        if len(sublist) > 1:
            prob = None
            #print(prob)
        if all(value == 'unknown' for value in list[0].values()):
            all_unknown = True
            print(str(idx) + str(list[0]))
        path = [list[0], list[3], list[1], all_unknown]
        if (all_unknown == False):
            all_paths.append(path)
    final_list.append([correct_label, all_paths, prob])

In [28]:
with open('../missing_feature/1_missing/dt_1_1_missing.json', 'w') as file:
    # Serialize list to JSON with indentation and write it to the file
    json.dump(final_list, file, indent=4)